In [ ]:
pip install jina

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.1/50.1 kB 2.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 153.9/153.9 kB 2.5 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
INFO: pip is looking at multiple versions of types-requests to determine which version is compatible with other requirements. This could take a while.
INFO: pip is still looking at multiple versions of types-requests to determine which version is compatible with other requirements. This could take a while.
INFO: This is taking longer than usual. You might need to provide the dependency resolver with stricter constraints to reduce runtime. See https://pip.pypa.io/warnings/backtracking for guidance. If you want to abort this run, press Ctrl + C.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.9/7.9 MB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 270.2/270.2 kB 21.1 MB/s eta 0:00

In [ ]:
import torch
import torch.nn.functional as F
from transformers import XGLMTokenizer, XGLMForCausalLM
import json
from jina import Document, DocumentArray, Flow
from jina.clients import Client
from jina import Executor, requests
from torch.utils.data import DataLoader
from tqdm import tqdm
import multiprocessing
from functools import partial

In [ ]:
# Load XGLM-2 tokenizer and model
tokenizer = XGLMTokenizer.from_pretrained("facebook/xglm-564M")
model = XGLMForCausalLM.from_pretrained("facebook/xglm-564M", output_hidden_states=True)

The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets. (raised from /usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94)


tokenizer_config.json:   0%|          | 0.00/433 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/4.92M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/276 [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.03M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/546 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.13G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/168 [00:00<?, ?B/s]

In [ ]:
import os

In [ ]:
from google.colab import files
uploaded = files.upload()

Saving extracted_text_data.json to extracted_text_data.json


In [ ]:
import io
file_name = "extracted_text_data.json"

# Open the file, read its content, and decode it as UTF-8
with open(file_name, 'r', encoding='utf-8') as f:
    file_content = f.read()

# Create a StringIO object from the file content
string_io_object = io.StringIO(file_content)


In [ ]:
file_path = r"extracted_text_data.json"
# extracted_data = json.load(open(file_path))

In [ ]:
print(file_path)

extracted_text_data.json


In [ ]:
extracted_data = json.load(open(file_path))

In [ ]:
print(extracted_data)

{'en': [{'filename': 'Blue_Ocean_Strategy,_Expanded_Edition_How_to_Create_Uncontested-2.pdf', 'text': 't h\n৬ 1 :\n1 ۱ \u200fسے\u200e\n\u200e一 一 一 E 5 \u200fہے ہے\u200e 一 -\n— 一 一 一 一\n= 一 — \u200fسے۔-\u200e = s\n_ “OW tO -reate \u200fجراے\u200e VII. tea Vie Ket space” 一 一\n一 一 \u200f۔--\u202b\u200e 一 一 - - =\n5 \u200fر\u200e be | এ পল v 英 s\nডে nd Make ine Compet Lion ifreieVant —\n\nEXPANDED EDITION OF THE\nINTERNATIONAL BESTSELLER\n\nBLUE\nOCEAN\n\nHow to Create Uncontested Market Space\nand Make the Competition 1٤1٢616٤۶\n\nBlue Ocean\nStrategy\n\nHow to Create Uncontested Market Space\nand Make the Competition Irrelevant\n\nW. Chan Kim\nRenée Mauborgne\n\nHARVARD BUSINESS REVIEW PRESS\nBOSTON, MASSACHUSETTS\nCopyright\n\nCopyright 2015 Harvard Business School Publishing Corporation\nAll rights reserved\n\nNo part of this publication may be reproduced, stored in or introduced into\na retrieval system, or transmitted, in any form, or by any means (electronic,\nmechanical, photocopyi

In [ ]:
def chunk_text(text, chunk_size=125):
    """
    Splits a given text into chunks of approximately `chunk_size` words.

    Parameters:
        text (str): The input text to chunk.
        chunk_size (int): The number of words per chunk.

    Returns:
        list: A list of text chunks.
    """
    # Split the text into words
    words = text.split()

    # Generate chunks of `chunk_size` words
    return [" ".join(words[i:i+chunk_size]) for i in range(0, len(words), chunk_size)]


In [12]:
# Progress bar callback for multiprocessing
def update_progress_bar(pbar):
    def callback(_):
        pbar.update()
    return callback

In [13]:
# Enable expandable segments
os.environ['PYTORCH_CUDA_ALLOC_CONF'] = 'expandable_segments:True'

In [ ]:
# Load model and tokenizer
device = 'cpu'

In [14]:
def embed_text_batch(texts, embedding_layer=-1, batch_size=4, accumulation_steps=1):
       embeddings = []
       data_loader = DataLoader(texts, batch_size=batch_size, shuffle=False)

       for i, batch in enumerate(tqdm(data_loader, desc="Processing batches", leave=False)):
           # Tokenize and move inputs to GPU
           inputs = tokenizer(batch, return_tensors='pt', truncation=True, padding=True, max_length=512)
           inputs = {key: value.to(device) for key, value in inputs.items()}

           # Ensure the model is on the correct device
           model.to(device)

           # Forward pass
           with torch.no_grad():
               outputs = model(**inputs)

           # Extract embeddings and accumulate
           hidden_states = outputs.hidden_states
           if hidden_states is not None:
               batch_embeddings = hidden_states[embedding_layer].mean(dim=1)
           else:
               raise ValueError("Hidden states are None. Check model configuration or input data.")

           embeddings.extend(batch_embeddings.detach().cpu().numpy())

           # Clear GPU cache periodically
           if (i + 1) % accumulation_steps == 0:
               torch.cuda.empty_cache()

       return embeddings

# Optimized function to process and store embeddings
def create_embeddings(data, batch_size=4):
    from jina import Document, DocumentArray  # Ensure Jina is installed

    documents = []
    for folder, folder_data in tqdm(data.items(), desc="Processing folders"):
        for file_data in folder_data:
            text_chunks = chunk_text(file_data['text'])

            # Process chunks in batches
            chunk_embeddings = embed_text_batch(text_chunks, batch_size=batch_size)

            # Create Document objects for each chunk and its embedding
            for chunk, embedding in zip(text_chunks, chunk_embeddings):
                doc = Document(text=chunk, embedding=embedding)
                documents.append(doc)

    document_array = DocumentArray(documents)
    return document_array


In [15]:
def store_embeddings(document_array):
    flow = Flow().add(uses="jinahub+docker://DocCache")  # Choose a suitable Jina executor for indexing
    with flow:
        flow.index(document_array)

In [17]:
import re

In [22]:
def clean_text(text):
    """
    Cleans the input text by removing unwanted characters, Unicode sequences,
    and repetitive patterns.
    """
    # Remove newline characters and backslashes
    text = text.replace("\n", " ").replace("\\", " ")

    # Remove specific unwanted sequences
    text = re.sub(r"\|\|", " ", text)  # Remove ||
    text = re.sub(r"\[U\+200E\]", " ", text)  # Remove [U+200E]

    # Remove specific dashes and repetitive patterns
    text = re.sub(r"[-—–]{2,}", " ", text)  # Sequences of dashes
    text = re.sub(r"[=]{2,}", " ", text)  # Sequences of equal signs

    # Remove unwanted Unicode characters like \u200f, \u200e, and similar
    text = re.sub(r"[\u200f\u200e]", "", text)

    # Remove sequences of Chinese/Japanese-like characters (一 一 一, etc.)
    text = re.sub(r"[\u4e00-\u9fff]+", " ", text)

    # Remove multiple spaces
    text = re.sub(r"\s{2,}", " ", text)

    # Strip leading and trailing whitespace
    text = text.strip()

    return text

In [23]:

def preprocess_data(data):
    """
    Cleans the text data in a nested dictionary format.
    Args:
        data (dict): Dictionary containing text data to preprocess.

    Returns:
        dict: Preprocessed data with cleaned text.
    """
    cleaned_data = {}
    for lang, documents in data.items():
        cleaned_documents = []
        for doc in documents:
            cleaned_text = clean_text(doc['text'])
            cleaned_documents.append({"filename": doc['filename'], "text": cleaned_text})
        cleaned_data[lang] = cleaned_documents
    return cleaned_data

In [24]:
preprocessed_data = preprocess_data(extracted_data)

In [25]:
print(preprocessed_data)

{'en': [{'filename': 'Blue_Ocean_Strategy,_Expanded_Edition_How_to_Create_Uncontested-2.pdf', 'text': 't h ৬ 1 : 1 ۱ سے E 5 ہے ہے - — = — سے۔- = s _ “OW tO -reate جراے VII. tea Vie Ket space” ۔ \u202b - - = 5 ر be | এ পল v s ডে nd Make ine Compet Lion ifreieVant — EXPANDED EDITION OF THE INTERNATIONAL BESTSELLER BLUE OCEAN How to Create Uncontested Market Space and Make the Competition 1٤1٢616٤۶ Blue Ocean Strategy How to Create Uncontested Market Space and Make the Competition Irrelevant W. Chan Kim Renée Mauborgne HARVARD BUSINESS REVIEW PRESS BOSTON, MASSACHUSETTS Copyright Copyright 2015 Harvard Business School Publishing Corporation All rights reserved No part of this publication may be reproduced, stored in or introduced into a retrieval system, or transmitted, in any form, or by any means (electronic, mechanical, photocopying, recording, or otherwise), without the prior permission of the publisher. Requests for permission should be directed to permissions@hbsp.harvard.edu, or ma

In [ ]:
document_array = create_embeddings(preprocessed_data)
# store_embeddings(document_array)

Processing batches: 100%|██████████| 165/165 [45:07<00:00, 14.86s/it]
                                                                     
Processing batches: 100%|██████████| 136/136 [37:48<00:00, 17.79s/it]
                                                                     
Processing batches:  85%|████████▍ | 66/78 [17:12<03:15, 16.25s/it]

Processing batches: 100%|██████████| 2/2 [00:36<00:00, 17.36s/it]
                                                                 
Processing batches: 100%|██████████| 1/1 [00:10<00:00, 10.67s/it]
                                                                 
Processing batches: 100%|██████████| 38/38 [12:33<00:00, 18.40s/it]
                                                                   
Processing batches: 100%|██████████| 1/1 [00:25<00:00, 25.82s/it]
                                                                 
Processing batches: 100%|██████████| 51/51 [16:13<00:00, 18.68s/it]
                                                   

Processing batches:   0%|          | 0/411 [00:00<?, ?it/s]FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead. (raised from <ipython-input-15-b116c11f328c>:15)

Processing documents: 100%|██████████| 22/22 [06:53<00:00, 18.79s/it]
